In [1]:
from openff.toolkit import Molecule, Topology, ForceField
from openff.interchange import Interchange
from openmm.unit import kelvin, picoseconds, nanometer, kilojoule, mole, dalton, angstrom, kilocalorie, nanosecond, femtosecond
from openmm import LangevinIntegrator, State, VerletIntegrator
from openmm.app import Simulation, DCDReporter, StateDataReporter, CheckpointReporter
from openmm.unit.quantity import Quantity
from sys import stdout
from IPython.display import HTML
import matplotlib.pyplot as plt
from matplotlib import animation
import numpy as np
import copy

In [2]:
from openmm.app.forcefield import ForceField as OpenMMForceField
from openmm.app import PDBFile

In [3]:
def animate_md(r:np.array, topology):
    # Setup the figure and axes...
    fig, ax = plt.subplots(figsize=(6,6))
    ax.set(xlim=(-3.5, 3.5), ylim=(-3.5, 3.5), ylabel='Angstrom',
           xlabel='Angstrom', title=f'{next(topology.molecules).name} movement')
    
    ## drawing and animating 
    scat = ax.scatter(r[0,:,0], r[0,:,1], marker='o', c=range(topology.n_atoms), s=1000)
    
    def animate(i):
        scat.set_offsets(r[100*i])
    
    ani = animation.FuncAnimation(fig, animate, frames=int(n/ 100))
    plt.close()
    return HTML(ani.to_jshtml())

In [4]:
### 3. Choose parameters of the experiment
temperature = 100*kelvin
frictionCoeff = 0  # 1/picoseconds
time_step = 0.0002*picoseconds
total_steps = int(1*picoseconds / time_step)

smiles_explicit_h = Molecule.from_smiles(
    #"[H][C]([H])([H])[C@@]([H])([C](=[O])[O-])[N+]([H])([H])[H]",
    "N1N=NN=N1",
    hydrogens_are_explicit=False,
)
smiles_explicit_h.generate_conformers(n_conformers=1)

sage = ForceField("openff_unconstrained-2.1.0.offxml")
interchange = Interchange.from_smirnoff(sage, [smiles_explicit_h])

positions = interchange.positions.to_openmm()
system = interchange.to_openmm_system()
topology = Topology.from_molecules([smiles_explicit_h])

original_positions = copy.deepcopy(interchange
                                   .to_openmm_simulation(
                                       LangevinIntegrator(temperature, frictionCoeff, time_step)
                                   )
                                   .context.getState(getPositions=True).getPositions())
original_positions_numpy = copy.deepcopy(interchange
                                   .to_openmm_simulation(
                                       LangevinIntegrator(temperature, frictionCoeff, time_step)
                                   )
                                   .context.getState(getPositions=True).getPositions(True))
positions[0][0] += Quantity(0.05, nanometer)

## MD with regular force terms

In [5]:
system_no_blf = interchange.to_openmm_system()
system_no_blf.removeForce(3)  # seems like bond length force is this one currently
integrator = VerletIntegrator(time_step)
simulation_no_blf = Simulation(topology.to_openmm(), system_no_blf, integrator)
simulation_no_blf.context.setPositions(positions)

In [6]:
bonds = sage.get_parameter_handler("Bonds").find_matches(topology)  # k units: kCal / Angstrom **2 / mole; length units: Angstrom
m = Quantity(np.array([[atom.mass.m] for atom in topology.atoms]), dalton)   # Dalton
def get_f(r, topology, bonds):
    f = Quantity(np.zeros_like(r), kilojoule/(nanometer*mole))
    for i in range(topology.n_atoms):
        for j in range(topology.n_atoms):
            if i != j and bonds.get((i,j)):
                rij = r[i] - r[j]
                rij_abs = np.linalg.norm(rij)
                k = bonds.get((i,j)).parameter_type.k.to_openmm()
                r0 = bonds.get((i,j)).parameter_type.length.to_openmm()
                f[i] -= k * (rij_abs - r0) * rij / rij_abs 
    return f


In [7]:
r = np.empty((total_steps, topology.n_atoms, 3)) 
for n in range(total_steps):
    state = simulation_no_blf.context.getState(getForces=True, 
                                               getPositions=True, 
                                               getVelocities=True, 
                                               getEnergy=True)
    f = get_f(state.getPositions(), topology, bonds)
    v = state.getVelocities() + f * time_step / m
    p = state.getPositions() + time_step * v
    simulation_no_blf.context.setPositions(p)
    simulation_no_blf.context.setVelocities(v)
    simulation_no_blf.step(1)
    r[n] = state.getPositions(True) * 10  # nanometer -> angstrom
    if n % 1000 == 0:
        #print(state.getForces())
        print(state.getKineticEnergy())
animate_md(r, topology)

0.051617104463949515 kJ/mol
221.73071269557235 kJ/mol
229.94850102441785 kJ/mol
128.8627264993445 kJ/mol
112.07890118699522 kJ/mol


## Add in linearized bond length force
Instead of using the bond length force provided by the Force Field, use the first order approximation $$F(R)\approx F(R_0) \nabla_{R}F(R_0)\cdot(R - R_0) = K\cdot(R - R_0) .$$
Here it is assumed that $F(R_0)=0$.

In [22]:
import scipy


def compute_jacobian(r_ini, topology):
    '''The function computes the Jacobian of the spring force evaluated
    at the initial positions of the particles.'''
    n = np.size(r_ini)
    K = Quantity(np.zeros((n, n)), kilocalorie / mole)
    for i in range(topology.n_atoms):
        for j in range(topology.n_atoms):
            if i == j:
                for other in np.arange(topology.n_atoms)[np.arange(topology.n_atoms) != i]:
                    RiRother = r_ini[i] - r_ini[other]
                    riother = np.linalg.norm(RiRother) ** 2
                    if bonds.get((i,other)):
                        k = bonds.get((i,other)).parameter_type.k.to_openmm()
                        r0 = bonds.get((i,other)).parameter_type.length.to_openmm() ** 2
                    else:
                        k = Quantity(0, kilocalorie / angstrom ** 2 / mole)
                        r0 = Quantity(0, nanometer) ** 2
                    l = 4 * k * Quantity(np.outer(RiRother, RiRother))
                    r = 2 * k * (riother - r0) * np.eye(3)
                    K[i * 3: (i+1) * 3, j * 3: (j+1) * 3] -= l + r
            else:
                RiRj = r_ini[i] - r_ini[j]
                rij = np.linalg.norm(RiRj) ** 2
                if bonds.get((i,j)):
                    k = bonds.get((i,j)).parameter_type.k.to_openmm()
                    r0 = bonds.get((i,j)).parameter_type.length.to_openmm() **2
                else:
                    k = Quantity(0, kilocalorie / angstrom ** 2 / mole)
                    r0 = Quantity(0, nanometer) **2
                l = 4 * k * Quantity(np.outer(RiRj,  RiRj))
                r = 2 * k * (rij - r0) * np.eye(3)
                K[i * 3: (i+1) * 3, j * 3: (j+1) * 3] = l + r 
    return K

def get_rotation(v, u):
    '''Compute an approximate rotation between two vectors.
    '''
    F = u.T @ np.array(v)  # .T turns Quantity into np.array. array @ Quantity not defined
    U, S, Vh = scipy.linalg.svd(F)
    R = Vh.T @ U.T
    return R

def get_repeated_rot(r_current, r_old, base_atom_idx, n_atoms, topology):
    '''Compute the rotation between the old positions r_old and the current positions r_current
    with respect to atoms bonded to the atom with base_atom_idx. Then insert that rotation block wise
    into a large rotation matrix for the entire molecule.
    '''
    RxLarge = np.zeros((n_atoms, n_atoms))
    Rx_invLarge = np.zeros((n_atoms, n_atoms))
    
    relevant_atoms = [base_atom_idx] + [bonded_atom.molecule_atom_index for
                            bonded_atom in topology.atom(base_atom_idx).bonded_atoms]
    Rx = get_rotation(r_current[relevant_atoms], r_old[relevant_atoms])
    RxLarge = np.kron(np.eye(n_atoms), Rx)
    Rx_invLarge = np.kron(np.eye(n_atoms), Rx.T)
    return Quantity(RxLarge), Quantity(Rx_invLarge), Quantity(Rx)

In [9]:
system_no_blf = interchange.to_openmm_system()
system_no_blf.removeForce(3)  # seems like bond length force is this one currently
integrator = VerletIntegrator(time_step)
simulation_no_blf = Simulation(topology.to_openmm(), system_no_blf, integrator)
simulation_no_blf.context.setPositions(positions)

In [10]:
K = compute_jacobian(original_positions, topology)
M_inv = np.kron(np.diag(1 / m.flatten()), np.eye(3))
f0 = get_f(original_positions, topology, bonds)

In [11]:
r = np.empty((total_steps, topology.n_atoms, 3)) 
for n in range(total_steps):
    state = simulation_no_blf.context.getState(getForces=True, 
                                               getPositions=True, 
                                               getVelocities=True, 
                                               getEnergy=True)
    p = state.getPositions(True)
    v = state.getVelocities(True)
    vv = state.getVelocities(True)
    for i in range(topology.n_atoms):
        QLarge, Q_invLarge, Q = get_repeated_rot(state.getPositions(True),
                                                original_positions_numpy,
                                                i, 
                                                topology.n_atoms)

        force_substitute = Quantity(
            Q @ (np.array(K) @ (Q_invLarge @ p.flatten() - original_positions_numpy.flatten()))[i*3 : (i+1)*3],
            kilojoule/(nanometer*mole))
        v[i] = vv[i] + time_step / m[i] * (force_substitute)
         #v = np.reshape(v_i_1, (topology.n_atoms,3))
    p = state.getPositions() + time_step * v
    simulation_no_blf.context.setPositions(p)
    simulation_no_blf.context.setVelocities(v)
    simulation_no_blf.step(1)
    r[n] = state.getPositions(True) * 10  # nanometer -> angstrom
    if n % 1000 == 0:
        #print(state.getForces())
        print(state.getKineticEnergy())
animate_md(r, topology)

0.051617104463949515 kJ/mol
72.07143378311234 kJ/mol
185.56868004874133 kJ/mol
246.9376419559851 kJ/mol
136.32983377545688 kJ/mol


## With global rotation approach
Use a rotation matrix $Q$ calculated from all atom positions in each step.

In [12]:
def get_Rx(r_current, r_old, topology):
    RxLarge = np.zeros((r_current.size, r_current.size))
    Rx_invLarge = np.zeros((r_current.size, r_current.size))
    for i in range(topology.n_atoms):
        relevant_atoms = list(range(topology.n_atoms))
        Rx = get_rotation(r_current[relevant_atoms], r_old[relevant_atoms])
        RxLarge[i*3: (i+1)*3, i*3: (i+1)*3] = Rx
        Rx_invLarge[i*3: (i+1)*3, i*3: (i+1)*3] = Rx.T
    return RxLarge, Rx_invLarge

In [13]:
system_no_blf = interchange.to_openmm_system()
system_no_blf.removeForce(3)  # seems like bond length force is this one currently
integrator = VerletIntegrator(time_step)
simulation_no_blf = Simulation(topology.to_openmm(), system_no_blf, integrator)
simulation_no_blf.context.setPositions(positions)

In [14]:
K = compute_jacobian(original_positions, topology)
M_inv = np.kron(np.diag(1 / m.flatten()), np.eye(3))
f0 = get_f(original_positions, topology, bonds)

In [15]:
r = np.empty((total_steps, topology.n_atoms, 3)) 
for n in range(total_steps):
    state = simulation_no_blf.context.getState(getForces=True, 
                                               getPositions=True, 
                                               getVelocities=True, 
                                               getEnergy=True)
    p = state.getPositions(True)
    v = state.getVelocities(True)
    QLarge, Q_invLarge = get_Rx(p, original_positions_numpy, topology)
    v = Quantity(v.flatten() + time_step * M_inv @ (QLarge @ np.array(K) @ \
        (Q_invLarge @ p.flatten() - original_positions_numpy.flatten())),
                 nanometer / picoseconds)
    
    v = v.reshape((topology.n_atoms,3))
    p = state.getPositions(True) + time_step * v
    simulation_no_blf.context.setPositions(p)
    simulation_no_blf.context.setVelocities(v)
    simulation_no_blf.step(1)
    r[n] = state.getPositions(True) * 10  # nanometer -> angstrom
    if n % 1000 == 0:
        #print(state.getForces())
        print(state.getKineticEnergy())
animate_md(r, topology)

0.051617104463949515 kJ/mol
73.34470496903116 kJ/mol
62.56808390434289 kJ/mol
70.40520336512084 kJ/mol
38.60101789782851 kJ/mol


## With warped rotation approach
Use atom wise calculated rotation matrices $Q_i$ in each iteration.

In [18]:
system_no_blf = interchange.to_openmm_system()
system_no_blf.removeForce(3)  # seems like bond length force is this one currently
integrator = VerletIntegrator(time_step)
simulation_no_blf = Simulation(topology.to_openmm(), system_no_blf, integrator)
simulation_no_blf.context.setPositions(positions)

In [19]:
K = compute_jacobian(original_positions, topology)
M_inv = np.kron(np.diag(1 / m.flatten()), np.eye(3))
f0 = get_f(original_positions, topology, bonds)

In [23]:
r = np.empty((total_steps, topology.n_atoms, 3)) 
for n in range(total_steps):
    state = simulation_no_blf.context.getState(getForces=True, 
                                               getPositions=True, 
                                               getVelocities=True, 
                                               getEnergy=True)
    p = state.getPositions(True)
    v = state.getVelocities(True)
    pp = np.empty_like(p)
    vv = np.empty_like(v)
    for i in range(topology.n_atoms):
        p = state.getPositions(True)
        v = state.getVelocities(True)
        QLarge, Q_invLarge, Q = get_repeated_rot(p, original_positions_numpy, 
                                              i, topology.n_atoms, topology)
        v = Quantity(v.flatten() + time_step * M_inv @ (QLarge @ np.array(K) @ \
            (Q_invLarge @ p.flatten() - original_positions_numpy.flatten())),
                     nanometer / picoseconds)
        
        v = v.reshape((topology.n_atoms,3))
        p = state.getPositions(True) + time_step * v
        vv[i] = v[i]
        pp[i] = p[i]
    simulation_no_blf.context.setPositions(pp)
    simulation_no_blf.context.setVelocities(vv)
    simulation_no_blf.step(1)
    r[n] = state.getPositions(True) * 10  # nanometer -> angstrom
    if n % 1000 == 0:
        #print(state.getForces())
        print(state.getKineticEnergy())
animate_md(r, topology)

0.051617104463949515 kJ/mol
72.07143378311234 kJ/mol
185.56868004874116 kJ/mol
246.93764195597123 kJ/mol
136.32983377511474 kJ/mol
